# Description of Functionality

# Algorithm

## Load settings from JSON file



In [ ]:
import os
from sys import argv
rootdir = argv[1]

#############################
#      FOR NOTEBOOK USE     #
#     SET DIRECTORY HERE    #
#                           #
#rootdir = ""
#                           #
#############################

print("Using root directory: {}".format(rootdir))

# Get the subdirs with the different tests
subdirs = sorted([ name for name in os.listdir('{}'.format(rootdir)) if os.path.isdir(os.path.join('{}'.format(rootdir), name)) ])
print("Available subdirs: {}".format(subdirs))

# Get subsubdirs with the several size shifts
subsubdirs = []
for subdir in subdirs:
    subsubdirs.append(sorted([ name for name in os.listdir('{}/{}'.format(rootdir, subdir)) if os.path.isdir(os.path.join('{}/{}'.format(rootdir, subdir), name)) ]))

print("Loaded all subsubdirs!")

In [ ]:
import json
from sys import exit

try:
    with open("{}/settings.json".format(rootdir)) as json_file:
        settings = json.load(json_file)
except:
    print("Please define a correct JSON file!")
    exit()

print("Succesfully loaded JSON file")

## Import
First, import the numpy library, initialize the arrays, and finally load the csv files. 

Because of the way the C script dumps the variables, the last character of the csv-file will be a comma and thus the last value of the `*_times` arrays will be `NaN`. Hence, the last value has to be eliminated.

In [ ]:
import numpy as np

# Initialize arrays
enq_send = []
recv = []

number_of_datapoints = 0

# Load all data and remove the last comma.
# This for loop distinguish between tests which measure the enqueue time and tests which
# measure the actual send time.
for i, subdir in enumerate(subdirs):
    enq_send.append([None] * len(subsubdirs[i]))
    recv.append([None] * len(subsubdirs[i]))
    for j, subsubdir in enumerate(subsubdirs[i]):
        enq_send[i][j] = np.genfromtxt('{}/{}/{}/enq_send_times.csv'.format(rootdir, subdir, subsubdir), delimiter=',')
        recv[i][j] = np.genfromtxt('{}/{}/{}/recv_times.csv'.format(rootdir, subdir, subsubdir), delimiter=',')
    
        # Remove last comma
        enq_send[i][j] = np.delete(enq_send[i][j], -1)
        recv[i][j] = np.delete(recv[i][j], -1)

        #Print number of datapoints
        print('Loaded {} + {} datapoints from {}/{}.'.format(np.size(enq_send[i][j]), np.size(recv[i][j]), subdir, subsubdir))


## Process data
Now, the data is processed. First, a check for overflows have to be performed. The timestamps are determined with the function `clock_gettime(clockid_t clk_id, const struct timespec *tp)`. Both the `struct tp`, as well as the function are showed below

```
struct timespec {
  time_t   tv_sec;        /* seconds */
  long     tv_nsec;       /* nanoseconds */
} tp;

clock_gettime(CLOCK_MONOTONIC, &tp);
```

The application only sends the `long tv_nsec` value, which goes from 999999999ns to 0ns. Since transmissions cannot take longer than 1 second, this overflow is resolved by adding 1000000000ns to the receive timestamps and the send confirmation timestamps, if they are smaller than the enqueue- or send timestamps.

Subsequentely, the deltas between the enqueue- or send time and the receive time, and the delta between the enqueue- or send time and the send confirmation time are calculated.

In [ ]:
# Initialize arrays
enq_send_recv_d = []
medians = []
upper_limit = []
lower_limit = []

# Resolve overflow issues and then calculate deltas
for i in range(0, len(subdirs)):
    medians.append([])
    upper_limit.append([])
    lower_limit.append([])
    for j in range(0, len(subsubdirs[i])):
        recv[i][j][recv[i][j] < enq_send[i][j]] += 1000000000

        medians[i].append(np.median(recv[i][j] - enq_send[i][j]))
        
        # np.sort(recv[i][j] - enq_send[i][j])[int(np.size(recv[i][j]]) / 2)] would be the approximately the median
        # Calculate upper 10% and lower 10%
        upper_limit[i].append(abs(medians[i][j] - np.sort(recv[i][j] - enq_send[i][j])[int(9 * np.size(recv[i][j]) / 10)]))
        lower_limit[i].append(abs(medians[i][j] - np.sort(recv[i][j] - enq_send[i][j])[int(1 * np.size(recv[i][j]) / 10)]))

## Plotting

The data will now be plotted.

In [ ]:
# Define "find nearest" function
def find_nearest(array, value):
    array = np.asarray(array)
    idx = (np.abs(array - value)).argmin()
    return array[idx], idx

In [ ]:
import matplotlib.pyplot as plt
from matplotlib.font_manager import FontProperties
import os

#First, delete all old plots and recreate the directory
os.system('rm -rf ./plots')
os.system('mkdir ./plots')

plots_saved = 0

#Start adding data
for i in range(0, len(subdirs)):
    y_data = np.array([])
    x_data = np.array([])

    for j in range(0, len(subsubdirs[i])):
        x_data = np.append(x_data, j)
        y_data = np.append(y_data, medians[i][j])
        
    if i in settings['iter_to_start_new_plot']:
        width = 1.125 * settings['dimensions']['figure'][0] if i == 0 else settings['dimensions']['figure'][0]
        fig = plt.figure(num=None, figsize=(width, settings['dimensions']['figure'][1]), dpi=500, facecolor='w', edgecolor='k')
        
        # Add plot and set title
        ax = fig.add_subplot(111)

    ax.errorbar(x_data, medians[i], yerr = [lower_limit[i], upper_limit[i]],
                capsize = 3.7, elinewidth = 1, markeredgewidth = 1, zorder = 2+i,
                color = settings['colors'][(i + settings['skip_label'][i]) % len(settings['colors'])],
                marker = settings['markers'][(i + settings['skip_label'][i]) % len(settings['markers'])],
                label = settings['labels'][(i + settings['skip_label'][i]) % len(settings['labels'])])

    if i in settings['iter_to_end_plot']:
        # Set grid
        ax.set_axisbelow(True)
        ax.grid(True, linestyle='--')

        # Generate plot
       
        #Labels
        font_text = FontProperties()
        font_text.set_size(9.5)
        font_text.set_family('monospace')

        # Set axis
        plt.xlim([0, settings['limits'][0]])
        plt.ylim([0, settings['limits'][1]])

        # Set ticks
        ticks_unmodified = ticks = np.arange(0, settings['limits'][0] + 1, 1.0)

        # Explicitly set labels
        labels = []
        for k in range(0,13):
            value = 8 * 2 ** k
            labels.append(str(value))

        # Set xticks
        plt.xticks(ticks, labels, fontsize=10.5, family='monospace', rotation=30, horizontalalignment='right', rotation_mode="anchor")
    
        if i == settings['iter_to_end_plot'][0]:
            ax.set_ylabel('$\\tilde{t}_{lat}$ [ns]', fontsize=11, family='monospace', labelpad=6)
        else:
            ax.get_yaxis().set_ticklabels([])

        # Set yticks
        plt.yticks(fontsize=10, family='monospace')

        ax.set_xlabel('message size [B]', fontsize=10.5, family='monospace', labelpad=4)

        ax.yaxis.grid(True, linestyle='-', which='major', color='black', alpha=0.8)
        ax.yaxis.grid(True, linestyle='--', which='minor', color='lightgrey', alpha=0.3)

        plt.minorticks_on()
        plt.tight_layout()

        # Save plot
        fig.savefig('{}/plot_{}.pdf'.format(rootdir, plots_saved), dpi=600, format='pdf')
        plots_saved += 1

        if i == settings['iter_to_end_plot'][0]:
            # Create and save legend
            import pylab

            # create a second figure for the legend
            figLegend = pylab.figure(figsize = settings['dimensions']['legend'])

            # produce a legend for the objects in the other figure
            pylab.figlegend(*ax.get_legend_handles_labels(), loc = 'upper left',
                            prop={'family':'monospace', 'size':'8'}, ncol=2)
            figLegend.savefig("{}/legend.pdf".format(rootdir), format='pdf')
            